### Minimal ensemble code

This code builds a simple bagging ensemble based on Kfold train/val split. Use it for quick idea testing with GPT-5-assisted tree generation. This notebook trains on top of TabPFN baseline

In [1]:
%env CUDA_VISIBLE_DEVICES=1
dataset_name = "credit-g"
results_path = f"tree_scores.{dataset_name}.json"

env: CUDA_VISIBLE_DEVICES=1


In [2]:
import os
import re
import json
import numpy as np
import pandas as pd
import openml
import smolagents
from huggingface_hub import login
import proxy_api_model
import prompting
import tree_agent
from sklearn.model_selection import train_test_split
from task import metric_func_by_task, get_task_variables, add_tabpfn_baseline
import dataset_descriptions

login(token=HF_TOKEN_HERE)
# V-- this uses a GPT-5 model over an API. Replace with https://smolagents.org/docs/agents-guided-tour/
model = proxy_api_model.ProxyAPIModel(
    model_id="gpt-5",
    api_base=API_ENDPOINT_HERE,  # <-- https://your/openai-like/api/v1/chat/completions
    api_key=API_TOKEN_HERE,  # <-- use your token
    max_new_tokens=1024 * 8,
    callback=lambda msg, **etc: print(  # print model thoughts before code
    re.sub(r'<code>.*?</code>', '<code omitted>', msg.content, flags=re.DOTALL))
)

# Load tabular benchmark
tabarena_version = "tabarena-v0.1"
benchmark_suite = openml.study.get_suite(tabarena_version)
task_ids = benchmark_suite.tasks
dataset_name_to_task_id = {}
for task_id in task_ids:
    task = openml.tasks.get_task(task_id)
    dataset = task.get_dataset()
    n_samples = dataset.qualities["NumberOfInstances"]
    if n_samples < 2_500:
        dataset_name_to_task_id[dataset.name] = task_id
        print(dataset.name, int(n_samples), task_id)

dataset_path = os.path.join("data", dataset_name)
assert not dataset_path.endswith('/')

airfoil_self_noise 1503 363612
anneal 898 363614
Another-Dataset-on-used-Fiat-500 1538 363615
blood-transfusion-service-center 748 363621
concrete_compressive_strength 1030 363625
credit-g 1000 363626
diabetes 768 363629
Fitness_Club 1500 363671
hazelnut-spread-contaminant-detection 2400 363674
healthcare_insurance_expenses 1338 363675
Is-this-a-good-customer 1723 363682
Marketing_Campaign 2240 363684
maternal_health_risk 1014 363685
qsar-biodeg 1054 363696
QSAR_fish_toxicity 907 363698
website_phishing 1353 363707
MIC 1699 363711


In [3]:
test_scores = []
for repeat_index in range(5):
    print("Beginning repeat", repeat_index)
    task = openml.tasks.get_task(dataset_name_to_task_id[dataset_name])
    data = add_tabpfn_baseline(**get_task_variables(task, fold=0, repeat=repeat_index))
    task_type = data['task_type']
    X_train, X_val, y_train, y_val, y_train_pred, y_val_pred = train_test_split(
        data["X_train"], data["y_train"], data["y_train_pred"], test_size=0.2, random_state=42,
        stratify=data['y_train'] if data['task_type'] != 'regression' else None
    )
    X_test, y_test, y_test_pred = data["X_test"], data["y_test"], data["y_test_pred"]

    result = tree_agent.TreeAgent(model=model).run(task=f"""
Build the optimal decision tree for the '{dataset_name}' dataset to improve upon a baseline non-tree model.
You are given access to 4 data variables in your python environment:
 - X_train, X_val are pandas dataframes with named feature columns (see below) that may need preprocessing;
 - y_train, y_val are numpy arrays (1d) with targets, also described below;
 - y_train_baseline, y_val_baseline are baseline model predictions (not a tree) that you want to improve upon.

Dataset description (use it to form hypotheses):
{dataset_descriptions.desc.get(dataset_name).format(num_samples=len(X_train), metric=prompting.metrics_by_task[task_type])}

Here's one way you could construct before you begin editing it manually:
{prompting.starter_snippets_by_task[task_type]}

**IMPORTANT:** your goal is not to predict the original target, but to improve upon a pre-existing baseline model.
The baseline predictions are accessible as y_train_bvaseline / y_var_baseline variables.
Baseline model predictions are also included as baseline_prediction_* columns in X_train/X_val, you may ignore or delete them if necessary.
Your model *must* work as follows:
```y_pred = y_baseline + your_tree.predict(X_with_possibly_engineered_features)```

To do so, you might want to start with a regression tree using (y_train - y_train_baseline) as target.
Your final returned tree (in `final_answer`) should only predict the difference that should be added to the baseline. The user will add your predictions to baseline on their side.

Now begin: view the data variables, preprocess as necessary, train a baseline tree, then propose the first hypothesis and start improving.
Focus on drawing conclusions from data, looking at the tree (e.g. via print) and using your own intuition about the problem for manual tree edits.
Quality is more important than speed: take as many steps as you need to get the best tree.
""".strip(), additional_args=dict(
            X_train=X_train.copy(), y_train=y_train.copy(), y_train_baseline=y_train_pred.copy(),
            X_val=X_val.copy(), y_val=y_val.copy(), y_val_baseline=y_val_pred.copy()
        ))
            
    y_pred_i = y_test_pred + result['model'].predict(result['preprocess_features'](X_test.copy()))
    if task_type == 'multiclass':  # normalize for logloss
        y_pred_i = y_pred_i / y_pred_i.sum(axis=-1, keepdims=True)
    test_score = metric_func_by_task[task_type](y_test, y_pred_i)
    print(f"Test {prompting.metrics_by_task[task_type]} score #{repeat_index}: {test_score:.5f}")
    test_scores.append(test_score)
    with open(results_path, "w") as f:
        json.dump(test_scores, f)

Beginning repeat 0
Inferred task type: binary


  0%|          | 0/10 [00:00<?, ?it/s]

Baseline train ROC AUC (sklearn.metrics.roc_auc_score) = 0.7579291845493563
Baseline test ROC AUC (sklearn.metrics.roc_auc_score) = 0.7770940170940172


╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ Build the optimal decision tree for the 'credit-g' dataset to improve upon a baseline non-tree model.           │
│ You are given access to 4 data variables in your python environment:                                            │
│  - X_train, X_val are pandas dataframes with named feature columns (see below) that may need preprocessing;     │
│  - y_train, y_val are numpy arrays (1d) with targets, also described below;                                     │
│  - y_train_baseline, y_val_baseline are baseline model predictions (not a tree) that you want to improve upon.  │
│                                                                                                                 │
│ Dataset description (use it to form hypotheses):                                                                │
│                                                                                                                 │
│ <dataset>                                                                                                       │
│ Your task is to predict whether a credit applicant is considered a good (lower risk) or bad (higher risk)       │
│ customer.                                                                                                       │
│ This dataset contains credit application records from a German bank, describing applicants’ financial and       │
│ personal situations.                                                                                            │
│                                                                                                                 │
│ Size: 532 total (train and val)                                                                                 │
│                                                                                                                 │
│ Feature descriptions:                                                                                           │
│ - `checking_status`: Categorical. Status of existing checking account ('<0', '0<=X<200', '>=200', 'no           │
│ checking').                                                                                                     │
│ - `duration_months`: Integer. Duration of loan in months.                                                       │
│ - `credit_history`: Categorical. Past credit repayment status.                                                  │
│ - `credit_purpose`: Categorical. Purpose of the loan (e.g. new car, repairs, education).                        │
│ - `credit_amount`: Float. Amount of credit requested.                                                           │
│ - `savings_status`: Categorical. Level of savings/bonds.                                                        │
│ - `employment_since`: Categorical. Current employment duration.                                                 │
│ - `installment_rate_percent`: Float. Installment rate as % of disposable income.                                │
│ - `personal_status_sex`: Categorical. Personal status and sex.                                                  │
│ - `other_debtors`: Categorical. Other debtors/guarantors.                                                       │
│ - `residence_since`: Integer. Duration at current residence (years).                                            │
│ - `property`: Categorical. Property/assets owned.                                                               │
│ - `age_years`: Integer. Applicant’s age.                                                                        │
│ - `other_installment_plans`: Categorical. Other installment plans (bank, stores, none).                         │
│ - `housing`: Categorical. Housing status (rent, own, f

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

...

Thought:
We found that a simple residual-correction tree using only the baseline prediction as input generalizes best. Larger feature sets or deeper trees overfit (validation AUC dropped). A depth-2 residual tree with large leaves (min_samples_leaf=80) provides a conservative, monotonic-like adjustment to the baseline and improves validation AUC from 0.7689 to 0.7902. I will finalize this tree and provide a minimal preprocessing function that selects baseline_prediction. I’ll recompute the final train/val AUCs as a sanity check and return the model.

<code omitted>


─ Executing parsed code: ──────────────────────────────────────────────────────────────────────────────────────── 
  from copy import deepcopy                                                                                        
  import pandas as pd                                                                                              
  from sklearn.metrics import roc_auc_score                                                                        
                                                                                                                   
  # Use the already trained best tree "final_tree" from the previous steps.                                        
                                                                                                                   
  def preprocess_features(X: pd.DataFrame):                                                                        
      X = deepcopy(X)                                                                                              
      # Ensure numeric baseline_prediction column                                                                  
      bp = pd.to_numeric(X["baseline_prediction"], errors="coerce")                                                
      # Fill any (unlikely) NaNs with the mean of provided input (no effect if none are NaN)                       
      bp = bp.fillna(bp.mean())                                                                                    
      return pd.DataFrame({"baseline_prediction": bp})                                                             
                                                                                                                   
  # Compute final metrics to report                                                                                
  Xtr_final = preprocess_features(X_train)                                                                         
  Xva_final = preprocess_features(X_val)                                                                           
  train_pred_final = y_train_baseline + final_tree.predict(Xtr_final)                                              
  val_pred_final = y_val_baseline + final_tree.predict(Xva_final)                                                  
  final_train_auc = roc_auc_score(y_train, train_pred_final)                                                       
  final_val_auc = roc_auc_score(y_val, val_pred_final)                                                             
                                                                                                                   
  final_answer({                                                                                                   
      "summary": "Residual-correction decision tree using only the baseline_prediction feature. The tree is        
  depth-2 with large leaves (min_samples_leaf=80), making conservative adjustments: it slightly increases          
  mid-range baseline scores and reduces overconfident high scores. This simple, stable residual model improved     
  validation AUC from 0.7689 to 0.7902, avoiding overfitting seen with richer feature sets. Potential next steps:  
  consider monotonic constraints or isotonic calibration, but current tree is intentionally small and robust.",    
      "train_score": float(final_train_auc),                                                                       
      "val_score": float(final_val_auc),                                                                           
      "model": final_tree,                                                                                         
      "preprocess_features": preprocess_features,                                                                  
  })                                                                                                               
 ────────────────────────────────────────────────────────

Final answer: {'summary': 'Residual-correction decision tree using only the baseline_prediction feature. The tree 
is depth-2 with large leaves (min_samples_leaf=80), making conservative adjustments: it slightly increases 
mid-range baseline scores and reduces overconfident high scores. This simple, stable residual model improved 
validation AUC from 0.7689 to 0.7902, avoiding overfitting seen with richer feature sets. Potential next steps: 
consider monotonic constraints or isotonic calibration, but current tree is intentionally small and robust.', 
'train_score': 0.7660282258064516, 'val_score': 0.790159574468085, 'model':  if baseline_prediction <= 0.772:  # 
id: 0, then id: 1, else id: 4, value: -0.008
  then: if baseline_prediction <= 0.675:  # id: 1, then id: 2, else id: 3, value: 0.014
    then: leaf value=-0.015  # id: 2
    else: leaf value=0.087  # id: 3
  else: if baseline_prediction <= 0.867:  # id: 4, then id: 5, else id: 6, value: -0.035
    then: leaf value=-0.095  # id: 5
    else: leaf value=-0.004  # id: 6, 'preprocess_features': <function create_function.<locals>.new_func at 
0x7fc1d00c4220>}

[Step 6: Duration 36.06 seconds| Input tokens: 28,971 | Output tokens: 13,247]

Test ROC AUC (sklearn.metrics.roc_auc_score) score #4: 0.79462


In [5]:
test_scores

[0.7780769230769231,
 0.7831196581196582,
 0.791025641025641,
 0.8126068376068377,
 0.7946153846153846]

In [6]:
np.mean(test_scores), np.std(test_scores,ddof=1)

(0.791888888888889, 0.013276691820390466)